In [23]:
# !pip install openai langchain python-dotenv -q

In [24]:
# !pip install chromadb==0.3.22 tiktoken -q

In [25]:
# !pip install chromadb -U

In [26]:
# !pip install gradio

In [27]:
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import Chroma
from langchain.text_splitter import CharacterTextSplitter
from langchain.chains.question_answering import load_qa_chain
from langchain.llms import OpenAI
import os


In [28]:
with open("/content/Data_Engineering.txt") as f:
    hitchhikersguide = f.read()

In [29]:
text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0, separator = "\n")
texts = text_splitter.split_text(hitchhikersguide)
print(f"Final lenght: {len(texts)}")

Final lenght: 1


In [30]:
### Setting up the OpenAI env

!echo OPENAI_API_KEY="" > .env

In [31]:
import os
import openai
from dotenv import load_dotenv

load_dotenv(".env")

openai.api_key = os.environ.get("OPENAI_API_KEY")

In [32]:
embeddings = OpenAIEmbeddings()

In [33]:
docsearch = Chroma.from_texts(texts, embeddings, metadatas=[{"source": str(i)} for i in range(len(texts))]).as_retriever()

In [34]:
# Creating the Chain Model
chain = load_qa_chain(OpenAI(temperature=0), chain_type="stuff")

In [35]:
def make_inference(query):
    docs = docsearch.get_relevant_documents(query)
    return(chain.run(input_documents=docs, question=query))

In [36]:
import gradio

if __name__ == "__main__":
    # make a gradio interface
    import gradio as gr

    gr.Interface(
        make_inference,
        [
            gr.inputs.Textbox(lines=2, label="Query"),
        ],
        gr.outputs.Textbox(label="Response"),
        title="🗣️TalkToMyDoc📄",
        description="🗣️TalkToMyDoc📄 is a tool that allows you to ask questions about a document. In this case - Hitch Hitchhiker's Guide to the Galaxy.",
    ).launch()

<ipython-input-36-636b02531079>:10: GradioDeprecationWarning: Usage of gradio.inputs is deprecated, and will not be supported in the future, please import your component from gradio.components
  gr.inputs.Textbox(lines=2, label="Query"),
<ipython-input-36-636b02531079>:10: GradioDeprecationWarning: `optional` parameter is deprecated, and it has no effect
  gr.inputs.Textbox(lines=2, label="Query"),
<ipython-input-36-636b02531079>:10: GradioDeprecationWarning: `numeric` parameter is deprecated, and it has no effect
  gr.inputs.Textbox(lines=2, label="Query"),
<ipython-input-36-636b02531079>:12: GradioDeprecationWarning: Usage of gradio.outputs is deprecated, and will not be supported in the future, please import your components from gradio.components
  gr.outputs.Textbox(label="Response"),


Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Note: opening Chrome Inspector may crash demo inside Colab notebooks.

To create a public link, set `share=True` in `launch()`.


<IPython.core.display.Javascript object>